# A Simple NEAT Implementation
Heavily based on: https://github.com/Code-Bullet/NEAT_Template

Original Paper: http://nn.cs.utexas.edu/downloads/papers/stanley.ec02.pdf

### Imports

In [135]:
import numpy as np
import copy
# for showing the game
import matplotlib.pyplot as plt
import matplotlib.animation
import IPython.display
from tqdm import tqdm
from colorama import Fore, Back, Style
import time

### Node Class

In [54]:
class Node():
    def __init__(self, num, layer, func):
        self.num = num
        self.func = func
        self.layer = layer
        self.connections_in_num = 0
        self.connections_out = []
        self.in_values = []
        self.done = False
        self.value = 0
    
    def eval(self, value, connection):
        # Checking if the connection is valid
        if connection.out_node != self:
            debug_print("{} not connected to Node {}".format(connection, self.num))
            return None
        
        self.in_values.append(value)
        
        # does not check if a connection submited something twice, so don't run the net agsin until it is done
        if len(self.in_values) != self.connections_in_num:
            self.done = False
            debug_print("Node: {} value recieve: {}, not complete".format(self.num, value))
        else:
            self.value = self.func(sum(self.in_values))
            debug_print("Node: {} value recieve: {}, complete".format(self.num, value))
            for connection in self.connections_out:
                connection.eval(self.value, self)
            self.done = True
            
    
    def reset(self):
        self.done = False
        self.in_values = []
        self.value = 0

### Connection Class
Connects two nodes, when it recives a value from one node it multiplies it by its weight and then evaluates the out node with that value

In [55]:
class Connection():
    def __init__(self, in_node, out_node, w, inno):
        self.in_node = in_node
        self.out_node = out_node
        self.weight = w
        self.innovation_num = inno
        self.enabled = True
    
    def mutate_weight(self, epsilon = .1):
        if np.random.random() < epsilon:
            self.weight = random()
        else:
            self.weight += np.random.normal()
        
        if self.weight > 1:
            self.weight = 1
        elif self.weight < -1:
            self.weight = -1
            
    def eval(self, value, node):
        if self.in_node != node:
            debug_print("Node {} is not connected to connection {}".format(node.num, self))
            return None
        elif self.enabled:
            self.out_node.eval(value*self.weight, self)
        else:
            return False

### The Actual Neural Net Class
This uses the Connection and Node class to create an actual Neural Net that can be Evaluated and Mutated etc.

In [176]:
class Net():
    def __init__(self, num_in, num_out):
        self.in_nodes = []
        self.out_nodes = []
        self.nodes = []
        
        self.connections = []
        
        self.functions = [sigmoid]
        self.fitness = 0
        
        self.next_node_num = 0
        self.next_connection_num = 0
        
        # in nodes
        for i in range(num_in):
            self.in_nodes.append(Node(self.next_node_num, 0, function))
            self.nodes.append(self.in_nodes[-1])
            self.next_node_num += 1
        
        self.bias_node = Node(self.next_node_num, 0, bias)
        self.nodes.append(self.bias_node)
        self.next_node_num += 1
        
        # out nodes
        for i in range(num_out):
            self.out_nodes.append(Node(self.next_node_num, 2, function))
            self.nodes.append(self.out_nodes[-1])
            self.next_node_num += 1
        
        # connecting all in nodes to out nodes
        for in_node in self.in_nodes:
            for out_node in self.out_nodes:
                self.connections.append(Connection(in_node, out_node, random(), self.next_connection_num))
                self.next_connection_num += 1
        
        #connecting bias node to out nodes
        for out_node in self.out_nodes:
            self.connections.append(Connection(self.bias_node, out_node, random(), self.next_connection_num))
            self.next_connection_num += 1
        
        # adding connections to nodes
        self.connect()
        
        #setting up input nodes to work
        for node in self.in_nodes:
            node.connections_in_num = 1
            
        self.bias_node.connections_in_num = 1
        
    def eval(self, in_values):
        
        out_values = []
        
        #inserting input values
        for i in range(len(self.in_nodes)):
            self.in_nodes[i].eval(in_values[i], Connection(None, self.in_nodes[i], 1, -1))
        
        self.bias_node.eval(0,  Connection(None, self.bias_node, 1, -1))
        
        for node in self.nodes:
            if node.connections_in_num < 1:
                node.eval(0, Connection(none, node, 1, -1))
        #making sure each node is done
        for node in self.nodes:
            count = 0
            while not node.done:
                time.sleep(0.001)
                count += 1
                if count == 10000:
                    print(self.string_connection(), end = '\r')
                pass
            print(self.string(), end = '\r')
            time.sleep(0.01)
            #debug_print("Node: {} done".format(node.num))
        #getting output values
        for node in self.out_nodes:
            out_values.append(node.value)
        
        self.reset()
        
        return out_values
    
    def reset(self):
        # Reset all nodes
        for node in self.nodes:
            node.reset()
    
    def connect(self):
        # Reset all connections of each node
        
        for node in self.nodes:
            node.connections_out = []
            node.connections_in_num = 0
        
        for connection in self.connections:
            if connection.in_node == connection.out_node:
                print("Faulty Connection: {} from {} to {}".format(connection.innovation_num, connection.in_node.num, connection.out_node.num))
                self.connections.remove(connection)
            elif connection.enabled:
                connection.in_node.connections_out.append(connection)
                connection.out_node.connections_in_num += 1
                
        for node in self.in_nodes:
            node.connections_in_num = 1
            
        self.bias_node.connections_in_num = 1
            
    def add_node(self, innovation_history):
        
        connection_old = np.random.choice(self.connections)
        while connection_old.in_node == self.bias_node:
            connection_old = np.random.choice(self.connections)
        
        connection_old.enabled = False
        
        new_node = Node(self.next_node_num, 1, np.random.choice(self.functions))
        self.next_node_num += 1
        self.nodes.append(new_node)
        debug_print("added node {}, between node {} and node {}".format(new_node.num, connection_old.in_node.num, connection_old.out_node.num))
        inno_num = -1
        # connection between old in node and new node
        connection = Connection(connection_old.in_node, new_node, 1, inno_num)
        connection.innovation_num = self.new_innovation_num(innovation_history, connection)
        self.connections.append(connection)
        debug_print("connected node {} to node {}".format(connection.in_node.num, connection.out_node.num))
        # connection between new node and old out node
        connection = Connection(new_node, connection_old.out_node, connection_old.weight, inno_num)
        connection.innovation_num = self.new_innovation_num(innovation_history, connection) # for this function the current inno num of the connection does not matter
        self.connections.append(connection)
        debug_print("connected node {} to node {}".format(connection.in_node.num, connection.out_node.num))
        # connection between bias node and new node
        connection = Connection(self.bias_node, new_node, 0, inno_num)
        connection.innovation_num = self.new_innovation_num(innovation_history, connection)
        self.connections.append(connection)
        debug_print("connected node {} to node {}".format(connection.in_node.num, connection.out_node.num))
        
        self.connect() # reconect everything so it works properly
        
    def add_connection(self, innovation_history):
        if self.fully_connected():
            print("Net {} fully connected, connection failed".format(self))
            return
        
        # looking for node pairs that are viable to connect. Not same node, not to an input node, not from an output node, not connected via another path to avoid circular calculations
        node_pairs = []
        for node_1 in (self.nodes):
            for node_2 in self.nodes:
                if (not (node_1 == node_2)) and (not (node_2.layer == 0)) and (not (node_1.layer == 2)) and (not self.connected(node_2, node_1)) and (not self.connected_directly(node_1, node_2)):
                    debug_print("Viable connection: {} to {}".format(node_1.num, node_2.num))
                    node_pairs.append([node_1, node_2])
        
        if not (len(node_pairs) > 0):
            debug_print("No non circular connections in net: {}".format(self))
            return
        # picking random pair
        idx = np.random.randint(len(node_pairs))
        node_pair = node_pairs[idx]
        # making connection
        connection = Connection(node_pair[0], node_pair[1], random(), -1)
        new_inno = self.new_innovation_num(innovation_history, connection)
        connection.innovation_num = new_inno
        self.connections.append(connection)
        
        print("Net: {}, made Connection {} between Node {} and Node {}, new_inno {}".format(self, connection.innovation_num, node_pair[0].num, node_pair[1].num, new_inno))
        
        self.connect() # reconnect everything so every node is properly connected
        
    def new_innovation_num(self, innovation_history, connection):
        # Checking if the innovation already exists, and gets the number
        for innovation in innovation_history[1:]: # first item in list is the global innovation number
            if (innovation[0] == connection.in_node.num) and (innovation[1] == connection.out_node.num):
                return innovation[2]
        
        # If not already an innovation add it to the history
        innovation_num = copy.copy(innovation_history[0]) 
        innovation_history.append([connection.in_node.num, connection.out_node.num, innovation_num])
        innovation_history[0] += 1
        return innovation_num
    
    def fully_connected(self):
        # Checks if the Net is fully connected
        for node in self.nodes:
            if (node.layer == 0) and (len(node.connections_out) < ((len(self.nodes) - len(self.in_nodes)) - 1)):
                debug_print("Node {} on layer {} not fully connected".format(node.num, node.layer))
                return False
            elif (node.layer == 2) and (node.connections_in_num < (len(self.nodes) - len(self.out_nodes))):
                debug_print("Node {} on layer {} not fully connected".format(node.num, node.layer))
                return False
            elif (node.layer == 1) and (node.connections_in_num + len(node.connections_out)) < len(self.nodes):
                debug_print("Node {} on layer {} not fully connected".format(node.num, node.layer))
                return False
        
        return True
    
    def connected(self, node_1, node_2):
        # checks if the two given nodes are connected in that direction via any series of connections
        debug_print("Called, is Node {} connected to Node {}".format(node_1.num, node_2.num))
        for connection in node_1.connections_out:
            if connection.out_node == node_2:
                debug_print("Connected!")
                return True
            elif connection.out_node in self.out_nodes:
                debug_print("Dead end")
            elif self.connected(connection.out_node, node_2):
                debug_print("Connected recieved")
                return True
        debug_print("Not Connected")
        return False
    
    def connected_directly(self, node_1, node_2):
        # checks if two nodes are connected directly.
        for connection in node_1.connections_out:
            if connection.out_node == node_2:
                return True
        
        return False
    
    def mutate(self, innovation_history, mutation_rate = [0.8, 0.05, 0.03]):
        # randomly mutates the net, mutations are based on example and rates given in paper
        print ("Mutate {}".format(self))
        rand = np.random.random()
        if rand < mutation_rate[0]:
            for connection in self.connections:
                connection.mutate_weight()
                
        rand = np.random.random()
        if rand < mutation_rate[1]:
            self.add_connection(innovation_history)
        
        rand = np.random.random()
        if rand < mutation_rate[2]:
            self.add_node(innovation_history)
        
    def get_innovation_nums(self):
        innovation_nums = []
        for connection in self.connection:
            innovation_nums.append(connection.innovation_num)
            
    def return_by_innovation(self, innovation_num):
        for connection in self.connections:
            if connection.innovation_num == innovation_num:
                return connection
            
        return None

    def string(self):
        string = ''
        string += "Net {}, In nodes: ".format(self)
        for node in self.in_nodes:
            if node.done:
                string += (Style.BRIGHT + Fore.WHITE + Back.GREEN + "Node {}".format(node.num))
            else:
                string += (Style.BRIGHT + Fore.WHITE + Back.RED + "Node {}".format(node.num))
            string += (Style.RESET_ALL + ' ')
        string += 'Nodes: '
        for node in self.nodes:
            if (not (node in self.out_nodes)) and (not (node in self.in_nodes)):
                if node.done:
                    string += (Style.BRIGHT + Fore.WHITE + Back.GREEN + "Node {}".format(node.num))
                else:
                    string += (Style.BRIGHT + Fore.WHITE + Back.RED + "Node {}".format(node.num))
                string += (Style.RESET_ALL + ' ')
        string += ('Out nodes: ')
        for node in self.out_nodes:
            if node.done:
                string += (Style.BRIGHT + Fore.WHITE + Back.GREEN + "Node {}".format(node.num))
            else:
                string += (Style.BRIGHT + Fore.WHITE + Back.RED + "Node {}".format(node.num))
            string += (Style.RESET_ALL + ' ')
        return string
    
    def string_connection(self):
        string = ''
        string += "Net {}, Connections: ".format(self)
        for connection in self.connections:
            if connection.enabled:
                string += (Fore.WHITE + Back.GREEN + "Connection: {}".format(connection.innovation_num))
            else:
                string += (Fore.WHITE + Back.RED + "Connection: {}".format(connection.innovation_num))
            string += (Style.RESET_ALL + ' ')
            if connection.in_node.done:
                string += (Style.BRIGHT + Fore.WHITE + Back.GREEN + "Node {}".format(connection.in_node.num))
            else:
                string += (Style.BRIGHT + Fore.WHITE + Back.RED + "Node {}".format(connection.in_node.num))
            string += (Style.RESET_ALL + ' to ')
            if connection.out_node.done:
                string += (Style.BRIGHT + Fore.WHITE + Back.GREEN + "Node {}".format(connection.out_node.num))
            else:
                string += (Style.BRIGHT + Fore.WHITE + Back.RED + "Node {}".format(connection.out_node.num))
            string += (Style.RESET_ALL + ' ')
        return string


## Trainer

Trains a set of neurasl networks

In [149]:
class Trainer():
    def __init__(self, pop, in_num, out_num):
        self.pop = pop
        self.nets = []
        
        for i in range(pop):
            self.nets.append(Net(in_num, out_num))
        
        self.species = speciate(self.nets)
        self.best_plays = []
        self.best_fitness_ever = 0
        self.best_fitness_history = []
        self.best_player_history = []
        self.innovation_history = [self.nets[0].next_connection_num]
            
    def run_individual(self, game):
        best_fitness = 0
        print("Run.")
        for net in self.nets:
            game.reset()
            while not game.is_dead():
                actions = net.eval(game.observe())
                action = actions.index(max(actions))
                game.act(action)
            net.fitness = game.get_fitness()
            if net.fitness > best_fitness:
                best_net = net
                best_play = game.history
                best_fitness = net.fitness
            #print("net_run")
        print('\033[K' + "done")
        self.best_fitness_history.append(best_fitness)
        self.best_player_history.append(best_net)
        if best_fitness > self.best_fitness_ever:
            self.best_play = best_play
            self.best_player_ever = best_net
            self.best_fitness_ever = best_fitness
        self.best_plays.append(best_play)
        
    def natural_selection(self):
        self.species = speciate(self.nets)
        #print(self.species)
        self.adjust_fitness()
        self.allocate_offspring(self.pop)
        self.kill()
        children = self.create_offspring()
        self.nets = children
        
    def kill(self):
        #kill the bottom half of each species
        for s in self.species:
            if s[-1] < 1: # is not allocated any offspring, so it dies
                self.species.remove(s)
            else:
                fitness = [n.fitness for n in s[:-1]]
                idx_sort = np.argsort(fitness)
                keep_idx = idx_sort[round(len(idx_sort)):]
                keep = [s[idx] for idx in keep_idx]
                s = keep + [s[-1]]
        
    def create_offspring(self):
        children = []
        children.append(copy.deepcopy(self.best_player_history[-1]))
        for s in self.species:
            for i in range(s[-1]):
                children.append(get_child(s[:-1], self.innovation_history))
        
        while len(children) < self.pop:
            children.append(get_child(self.species[np.random.choice(range(len(self.species)))][:-1], self.innovation_history))
            
        return children
            
    
    # Fitness sharing
    def adjust_fitness(self):
        for s in self.species:
            size = len(s)
            for net in s:
                net.fitness = net.fitness/size
                
    def allocate_offspring(self, num_offspring):
        total_fitness = 0
        for net in self.nets:
            total_fitness += net.fitness
        
        for s in self.species:
            species_fitness = 0
            for net in s:
                species_fitness += net.fitness
            s.append(int(round(num_offspring * (species_fitness/total_fitness))))
            
    def train(self, num_generations, game):
        for i in range(num_generations):
            self.run_individual(game)
            self.natural_selection()
    
    def replay_best(self, game):
        observations = []
        for play in self.best_plays:
            observations = observations + play
            
        fig = plt.figure()
        image = plt.imshow(np.zeros((game.grid_size, game.grid_size)),interpolation='none', animated=True, vmin=0, vmax=1, cmap = 'gray')
    
        def animate(observation):
            image.set_array(observation.reshape((game.grid_size, game.grid_size)))
            return [image]
        
        self.best_plays = []
        animation = matplotlib.animation.FuncAnimation(fig, animate, frames=observations, blit=True)
        return animation
    


## K-mediods clustering PAM

Paper Used: https://www.cs.umb.edu/cs738/pam1.pdf

In [167]:
# several ways to improve efficiency?

def cluster(objs, num_clusters, dist_func):
    # innitialize Mediods (S)
    objects = copy.deepcopy(objs)
    best_mediod = objects[0]
    best_sum = 0
    for obj in objects:
        best_sum += dist_func(best_mediod, obj)
    for obj_1 in objects:
        sum = 0
        for obj_2 in objects:
            sum += dist_func(obj_1, obj_2)
        if sum < best_sum:
            best_sum = sum
            best_mediod = obj_1
    
    objects.remove(best_mediod)
    mediods = [best_mediod]
    if num_clusters < 2:
        return [mediods + objects]
    clusters = [[]]
    # Populating Mediods
    for i in range(num_clusters - 1):
        best_mediod = objects[0]
        best_sum = 0
        for obj_1 in objects:
            sum = 0
            for obj_2 in objects:
                if obj_2 != obj_1:
                    sum += max(closest_dist(obj, mediods, dist_func) - dist_func(obj, best_mediod), 0)
            if sum > best_sum:
                best_sum = sum
                best_mediod = obj
                
        objects.remove(best_mediod)
        mediods.append(best_mediod)
        clusters.append([])
    
    for i in range(len(objects)):
        objects[i] = [objects[i], 0, 0]
    
    #debug_print("starting Mediods: {}".format(mediods))
    # SWAP Part
    done = False
    round = 0
    while not done:
        objects = recalculate(objects, mediods, dist_func)
        round += 1
        print("round {}:".format(round), end = ' ')
        min_swap_cost = 0
        for mediod in mediods:
            for obj_1 in objects:
                swap_cost = 0
                for obj_2 in objects:
                    if obj_2 != obj_1:
                        if dist_func(obj_2[0], mediod) > obj_2[1]: # Case 1
                            contrib = min(dist_func(obj_2[0], obj_1[0]) - obj_2[1], 0)
                        else: 
                            contrib = min(dist_func(obj_2[0], obj_1[0]), obj_2[2]) - obj_2[1]
                        swap_cost += contrib
                #print ("Swap cost for swapping {} and {} is {}".format(mediod, obj_1, swap_cost))
                if swap_cost < min_swap_cost:
                    best_pair = [mediod, obj_1]
                    min_swap_cost = swap_cost
                #print("min swap cost: {}".format(min_swap_cost))
        if min_swap_cost < 0:
            mediods.remove(best_pair[0])
            objects.append([best_pair[0], 0, 0])
            objects.remove(best_pair[1])
            mediods.append(best_pair[1][0])
            print("Swaping {} and {}. Swap cost: {}".format(best_pair[0], best_pair[1][0], min_swap_cost), end = ' ')
        else:
            done = True
            print("done.", end='')
            #debug_print("done")
    print('')
    
    for i in range(len(clusters)):
        clusters[i].append(mediods[i])
    for obj in objects:
        mediod = closest(obj[0], mediods, dist_func)
        for cluster in clusters:
            if mediod in cluster:
                cluster.append(obj[0])
                
    return clusters
    
                            
                
def closest(obj, objects, dist_func):
    best_obj = objects[0]
    best_dist = dist_func(obj, best_obj)
    for obj_2 in objects:
        dist = dist_func(obj, obj_2)
        if dist < best_dist:
            best_dist = dist
            best_obj = obj_2
    
    return best_obj

def closest_dist(obj, objects, dist_func):
    return dist_func(obj, closest(obj, objects, dist_func))
    

def second_closest_dist(obj, objects, dist_func):
    objects_local = copy.deepcopy(objects)
    objects_local.remove(closest(obj, objects_local, dist_func))
    return dist_func(obj, closest(obj, objects_local, dist_func))

def recalculate(objects, mediods, dist_func):
    for obj in objects:
        obj[1] = closest_dist(obj[0], mediods, dist_func)
        obj[2] = second_closest_dist(obj[0], mediods, dist_func)
    return objects

# Testing
def dist(a, b):
    x = a[0] - b[0]
    y = a[1] - b[1]
    return (x**2 + y**2)**.5

a = []
for i in np.linspace(0, 1, num = 30, endpoint=False):
    for n in np.linspace(0, 1, num = 30, endpoint=False):
        a.append([i, n])

cluster(a, 3,  dist)

round 1: Swaping [0.0, 0.0] and [0.7666666666666666, 0.26666666666666666]. Swap cost: -53.39465908259115 round 2: Swaping [0.4666666666666667, 0.5] and [0.4, 0.7]. Swap cost: -22.55410559480401 round 3: Swaping [0.0, 0.03333333333333333] and [0.23333333333333334, 0.23333333333333334]. Swap cost: -22.860918354704868 round 4: Swaping [0.4, 0.7] and [0.4666666666666667, 0.7666666666666666]. Swap cost: -2.5308407248589075 round 5: Swaping [0.23333333333333334, 0.23333333333333334] and [0.23333333333333334, 0.3]. Swap cost: -0.5701135320601822 round 6: Swaping [0.7666666666666666, 0.26666666666666666] and [0.7666666666666666, 0.3]. Swap cost: -0.23466276524761262 round 7: Swaping [0.23333333333333334, 0.3] and [0.23333333333333334, 0.26666666666666666]. Swap cost: -0.12477482581700369 round 8: done.


[[[0.4666666666666667, 0.7666666666666666],
  [0.0, 0.7],
  [0.0, 0.7333333333333333],
  [0.0, 0.7666666666666666],
  [0.0, 0.8],
  [0.0, 0.8333333333333334],
  [0.0, 0.8666666666666667],
  [0.0, 0.9],
  [0.0, 0.9333333333333333],
  [0.0, 0.9666666666666667],
  [0.03333333333333333, 0.6666666666666666],
  [0.03333333333333333, 0.7],
  [0.03333333333333333, 0.7333333333333333],
  [0.03333333333333333, 0.7666666666666666],
  [0.03333333333333333, 0.8],
  [0.03333333333333333, 0.8333333333333334],
  [0.03333333333333333, 0.8666666666666667],
  [0.03333333333333333, 0.9],
  [0.03333333333333333, 0.9333333333333333],
  [0.03333333333333333, 0.9666666666666667],
  [0.06666666666666667, 0.6666666666666666],
  [0.06666666666666667, 0.7],
  [0.06666666666666667, 0.7333333333333333],
  [0.06666666666666667, 0.7666666666666666],
  [0.06666666666666667, 0.8],
  [0.06666666666666667, 0.8333333333333334],
  [0.06666666666666667, 0.8666666666666667],
  [0.06666666666666667, 0.9],
  [0.066666666666666

### General Functions
Functions that are used elswhere to make it easier and the crossover function that "mates" two Nets based on the method in the paper.

needs cleaning up

In [169]:
def random():
    return (np.random.random() - 0.5) * 2

def function(x):
    return x

def sigmoid(x):
    return 1/(1 + np.exp(-4.9*x))

def bias(x):
    return 1

def crossover(net_1, net_2): # net_1 is the more fit parent
    child = Net(len(net_1.in_nodes), len(net_1.out_nodes))
    #the child will have the same input and output structure as net_1
    child.connections = []
    
    for connection_1 in net_1.connections:
        # selecting connection to copy over
        connection_2 = net_2.return_by_innovation(connection_1.innovation_num)
        if connection_2 != None:
            if np.random.random() < 0.5:
                connection = connection_1
            else:
                connection = connection_2
        else:
            connection = connection_1
        
        # making nodes to add to connection and child
        is_enabled = True
        in_node = None
        out_node = None
        
        if (not (connection.enabled)) and np.random.random() < .75:
            is_enabled = False
        
        for node in child.nodes:
            if node.num == connection.in_node.num:
                in_node = node
            if node.num == connection.out_node.num:
                out_node = node
        
        if not in_node:
            in_node = copy.deepcopy(connection.in_node)
            child.nodes.append(in_node)
        
        if not out_node:
            out_node = copy.deepcopy(connection.out_node)
            child.nodes.append(out_node)
        
        # Making Connection
        connection = Connection(in_node, out_node, copy.copy(connection.weight), copy.copy(connection.innovation_num))
        connection.enabled = copy.copy(is_enabled)
        child.connections.append(connection)
    
    child.connect()
    
    return child

#dist function for distance between nets
def net_dist(net_1, net_2, weights = [1, 0.5]): # weights based on those used in paper
    normalizer = max(len(net_1.connections), len(net_2.connections)) - 20
    if normalizer < 1:
        normalizer = 1
    return (weights[0] * num_disjoint_excess(net_1, net_2) / normalizer) + (weights[1] * average_weight_diff(net_1, net_2))

# used to find the dist between nets
def average_weight_diff(net_1, net_2):
    total_diff = 0
    count = 0
    for connection_1 in net_1.connections:
        connection_2 = net_2.return_by_innovation(connection_1.innovation_num)
        if connection_2:
            count += 1
            total_diff += abs(connection_1.weight - connection_2.weight)
    
    if count == 0:
        return 0
    
    return total_diff/count

#used to find distance between nets
def num_disjoint_excess(net_1, net_2):
    count = 0
    for connection_1 in net_1.connections:
        connection_2 = net_2.return_by_innovation(connection_1.innovation_num)
        if connection_2:
            count += 1
    
    return (len(net_1.connections) + len(net_2.connections) - 2*count)

#returns the nets in species
def speciate(nets, threshold = 3):
    # first use method outlined in paper to find the # of species we want
    species = []
    for net in nets:
        found = False
        for s in species:
            if (not found) and (net_dist(net, s[0]) < threshold):
                s.append(net)
                found = True
                break
        if not found:
            species.append([net])
    num = len(species)
    if num < 2:
        num = 2
    print("speciate: {}".format(num))
    #print(len(species))
    # then use that number to cluster the nets
    return cluster(nets, num, net_dist)

def select_net_weighted(nets):
    total_fitness = 0
    for net in nets:
        total_fitness += net.fitness
    
    rand = total_fitness * np.random.random()
    
    moving_total = 0
    for net in nets:
        moving_total += net.fitness
        if moving_total > rand:
            return net
        
def get_child(species, innovation_history):
    if np.random.random() < .25:
        child = select_net_weighted(species)
    else:
        parent_1 = select_net_weighted(species)
        parent_2 = select_net_weighted(species)
        
        if parent_1.fitness > parent_2.fitness:
            child = crossover(parent_1, parent_2)
        else:
            child = crossover(parent_2, parent_1)
    
    child.mutate(innovation_history)
    return child

def debug_print(var):
    global debug
    if debug:
        print (var)
    

## Sample Game: Snake

In [73]:
class Snake(object):
    def __init__(self, grid_size = 45, max_moves_multiplyer = 1):
        self.max_moves = (grid_size**2) *  max_moves_multiplyer
        self.grid_size = grid_size
        snake = [[int(grid_size/2), int(grid_size/2)]]
        snake.append([snake[0][0] - 1, snake[0][1]])
        snake.append([snake[0][0] - 2, snake[0][1]])
        snake.append([snake[0][0] - 3, snake[0][1]])
        fruit_x = np.random.randint(0, grid_size)
        fruit_y = np.random.randint(0, grid_size)
        move = 0
        move_total = 0
        catch_count = 0
        self.history = []
        self.state = [[fruit_x, fruit_y], snake, [move, move_total, catch_count]]
    
    def _update_state(self, action):
        [fruit_x, fruit_y], snake, [move, move_total, catch_count] = self.state
        
        direction = [snake[0][0] - snake[1][0], snake[0][1] - snake[1][1]]
        if action == 0:
            movement = [1, 0] # Forward
        elif action == 1:
            movement = [0, -1] # Right
        elif action == 2:
            movement = [-1, 0] # Down
        elif action == 3:
            movement = [0, 1]
        else:
            raise Exception('Invalid action {}'.format(action))
        
        snake_new = [np.add(snake[0], movement).tolist()] + snake
        
        if [fruit_x, fruit_y] not in snake_new:
            snake_new = snake_new[:-1]
        #print("move: {}, action {}".format(move_total, action))
        #print("Snake: {}".format(snake))
        self.state = [[fruit_x, fruit_y], snake_new, [move + 1, move_total + 1, catch_count]]
        
    def _draw_state(self):
        
        im_size = (self.grid_size, self.grid_size)
        canvas = np.zeros(im_size)
        
        [fruit_x, fruit_y], snake, [move, move_total, catch_count] = self.state
        canvas[fruit_y, fruit_x] = 1 # draw fruit
        for coord in snake:
            try:
                canvas[coord[1]][coord[0]] = 1
            except IndexError:
                pass
            
        return canvas
        
    def act(self, action):
        self._update_state(action)
        self._update_score()
        self.history.append(self._draw_state())
        
    def get_fitness(self):
        [fruit_x, fruit_y], snake, [move, move_total, catch_count] = self.state
        return catch_count + np.log10(move_total)
    
    def _update_score(self):
        [fruit_x, fruit_y], snake, [move, move_total, catch_count] = self.state
        if [fruit_x, fruit_y] in snake:
            indices = []
            for i in np.indices((self.grid_size, self.grid_size)).swapaxes(0,2).swapaxes(0,1).reshape((self.grid_size**2, 2)):
                if not any((i == x).all() for x in snake):
                    indices.append(i)
            fruit = np.random.randint(0, len(indices))
            [fruit_x, fruit_y] = indices[fruit]
            self.state = [[fruit_x, fruit_y], snake, [0, move_total, catch_count + 1]]
            
    
    def is_dead(self):
        
        [fruit_x, fruit_y], snake, [move, move_total, catch_count] = self.state
        if snake[0] in snake[1:]:
            return True # it hit itself
        if snake[0][0] < 0 or snake[0][0] > self.grid_size - 1 or snake[0][1] < 0 or snake[0][1] > self.grid_size - 1:
            return True # it hit a wall
        if move > (self.max_moves) + (len(snake)):
            return True # ran out of time
        
        
        return False # not dead
    
    def observe_individual_dir(self, direction):
        [fruit_x, fruit_y], snake, [move, move_total, catch_count] = self.state
        
        distances = [0, 0, 0]
        
        pos = [snake[0][0] + direction[0], snake[0][1] + direction[1]]
        dist = 1
        snake_found = False
        fruit_found = False
        
        while not (pos[0] < 0 or pos[0] > self.grid_size - 1 or pos[1] < 0 or pos[1] > self.grid_size - 1):
            if (pos[0] == fruit_x) and (pos[1] == fruit_y) and not fruit_found:
                distances[2] = 1/dist
                fruit_found = True
            
            if (pos in snake) and not snake_found:
                distances[1] = 1/dist
                snake_found = True
            
            pos[0] += direction[0]
            pos[1] += direction[1]
            dist += 1
        
        distances[0] = 1/dist
        return distances
    
    def observe(self):
        return self.observe_individual_dir([0, 1]) + self.observe_individual_dir([1, 1]) + self.observe_individual_dir([1, 0]) + self.observe_individual_dir([1, -1]) + self.observe_individual_dir([0, -1]) + self.observe_individual_dir([-1, -1]) + self.observe_individual_dir([-1, 0]) + self.observe_individual_dir([-1, 1])
    
    def reset(self):
        
        snake = [[int(self.grid_size/2), int(self.grid_size/2)]]
        snake.append([snake[0][0] - 1, snake[0][1]])
        snake.append([snake[0][0] - 2, snake[0][1]])
        snake.append([snake[0][0] - 3, snake[0][1]])
        fruit_x = np.random.randint(0, self.grid_size)
        fruit_y = np.random.randint(0, self.grid_size)
        move = 0
        move_total = 0
        catch_count = 0
        self.state = [[fruit_x, fruit_y], snake, [move, move_total, catch_count]]
        self.history = []

### Testing

In [177]:
debug = False


# net_1 = Net(2, 2)
# net_2 = Net(2, 2)
# history = [5]

# print (net_1.eval([1, 2]))

# net_1.add_node(history)
# net_1.add_connection(history)

# net_3 = crossover(net_1, net_2)

# print (net_1.eval([1, 2]))
# print (net_2.eval([1, 2]))
# print (net_3.eval([1, 2]))

trainer = Trainer(10, 24, 4)

snake = Snake(grid_size = 10)
trainer.train(100, snake)

animation = trainer.replay_best(snake)
IPython.display.HTML(animation.to_jshtml())

speciate: 2
round 1: Swaping <__main__.Net object at 0x10bfb87f0> and <__main__.Net object at 0x10bf4e8d0>. Swap cost: -0.023617074283575235 round 2: done.
Run.
donemain__.Net object at 0x10bbb1c88>, In nodes: Node 0 Node 1 Node 2 Node 3 Node 4 Node 5 Node 6 Node 7 Node 8 Node 9 Node 10 Node 11 Node 12 Node 13 Node 14 Node 15 Node 16 Node 17 Node 18 Node 19 Node 20 Node 21 Node 22 Node 23 Nodes: Node 24 Out nodes: Node 25 Node 26 Node 27 Node 28 
speciate: 2
round 1: Swaping <__main__.Net object at 0x10bd39748> and <__main__.Net object at 0x10d8cd470>. Swap cost: -0.023617074283575235 round 2: done.
Mutate <__main__.Net object at 0x10bcb4438>
Mutate <__main__.Net object at 0x10d8cd470>
Mutate <__main__.Net object at 0x10d1909e8>
Net <__main__.Net object at 0x10d1909e8> fully connected, connection failed
Mutate <__main__.Net object at 0x10d8cd470>
Mutate <__main__.Net object at 0x10d8cd470>
Mutate <__main__.Net object at 0x10d227c50>
Mutate <__main__.Net object at 0x10d422780>
Mutate <_

donemain__.Net object at 0x10d347a58>, In nodes: Node 0 Node 1 Node 2 Node 3 Node 4 Node 5 Node 6 Node 7 Node 8 Node 9 Node 10 Node 11 Node 12 Node 13 Node 14 Node 15 Node 16 Node 17 Node 18 Node 19 Node 20 Node 21 Node 22 Node 23 Nodes: Node 24 Out nodes: Node 25 Node 26 Node 27 Node 28 
speciate: 2
round 1: done.
Mutate <__main__.Net object at 0x10d4e8f28>
Mutate <__main__.Net object at 0x10ca21160>
Mutate <__main__.Net object at 0x10bd98ac8>
Mutate <__main__.Net object at 0x10c668390>
Mutate <__main__.Net object at 0x10bd39748>
Mutate <__main__.Net object at 0x10bc0da58>
Mutate <__main__.Net object at 0x10b99c080>
Mutate <__main__.Net object at 0x10d753e10>
Mutate <__main__.Net object at 0x10bb66908>
Run.
donemain__.Net object at 0x10bb66908>, In nodes: Node 0 Node 1 Node 2 Node 3 Node 4 Node 5 Node 6 Node 7 Node 8 Node 9 Node 10 Node 11 Node 12 Node 13 Node 14 Node 15 Node 16 Node 17 Node 18 Node 19 Node 20 Node 21 Node 22 Node 23 Nodes: Node 24 Out nodes: Node 25 Node 26 Node 27 N

done
speciate: 2


round 1: Swaping <__main__.Net object at 0x10c067208> and <__main__.Net object at 0x10c691240>. Swap cost: -0.14040980697279598 round 2: done.
Mutate <__main__.Net object at 0x10d7fdda0>
Mutate <__main__.Net object at 0x10d1909e8>
Net <__main__.Net object at 0x10d1909e8> fully connected, connection failed
Mutate <__main__.Net object at 0x10d168c18>
Mutate <__main__.Net object at 0x10c9baba8>
Mutate <__main__.Net object at 0x10d184be0>
Mutate <__main__.Net object at 0x10ca24470>
Mutate <__main__.Net object at 0x10d78fdd8>
Mutate <__main__.Net object at 0x10bbd2630>
Mutate <__main__.Net object at 0x10c673da0>
Run.
donemain__.Net object at 0x10c673da0>, In nodes: Node 0 Node 1 Node 2 Node 3 Node 4 Node 5 Node 6 Node 7 Node 8 Node 9 Node 10 Node 11 Node 12 Node 13 Node 14 Node 15 Node 16 Node 17 Node 18 Node 19 Node 20 Node 21 Node 22 Node 23 Nodes: Node 24 Out nodes: Node 25 Node 26 Node 27 Node 28 
speciate: 2
round 1: Swaping <__main__.Net object at 0x10d57bdd8> and <__main__.Net object

round 1: Swaping <__main__.Net object at 0x10c9baba8> and <__main__.Net object at 0x10c776400>. Swap cost: -0.019906417888337358 round 2: Swaping <__main__.Net object at 0x10c776400> and <__main__.Net object at 0x10d7fdda0>. Swap cost: -0.025342066300277133 round 3: Swaping <__main__.Net object at 0x10d7fdda0> and <__main__.Net object at 0x10bbd2630>. Swap cost: -0.0436880834128488 round 4: Swaping <__main__.Net object at 0x10bbd2630> and <__main__.Net object at 0x10bd2f518>. Swap cost: -0.045621774431190365 round 5: Swaping <__main__.Net object at 0x10bd2f518> and <__main__.Net object at 0x10c776400>. Swap cost: -0.0038451724553718036 round 6: Swaping <__main__.Net object at 0x10c776400> and <__main__.Net object at 0x10d7fdda0>. Swap cost: -0.025342066300277133 round 7: Swaping <__main__.Net object at 0x10d7fdda0> and <__main__.Net object at 0x10bbd2630>. Swap cost: -0.0436880834128488 round 8: Swaping <__main__.Net object at 0x10bbd2630> and <__main__.Net object at 0x10bd2f518>. Swap

...

round 8822: Swaping <__main__.Net object at 0x10c776400> and <__main__.Net object at 0x10d7fdda0>. Swap cost: -0.025342066300277133 round 8823: Swaping <__main__.Net object at 0x10d7fdda0> and <__main__.Net object at 0x10bbd2630>. Swap cost: -0.0436880834128488 round 8824: Swaping <__main__.Net object at 0x10bbd2630> and <__main__.Net object at 0x10bd2f518>. Swap cost: -0.045621774431190365 round 8825: Swaping <__main__.Net object at 0x10bd2f518> and <__main__.Net object at 0x10c776400>. Swap cost: -0.0038451724553718036 round 8826: Swaping <__main__.Net object at 0x10c776400> and <__main__.Net object at 0x10d7fdda0>. Swap cost: -0.025342066300277133 round 8827: Swaping <__main__.Net object at 0x10d7fdda0> and <__main__.Net object at 0x10bbd2630>. Swap cost: -0.0436880834128488 round 8828: Swaping <__main__.Net object at 0x10bbd2630> and <__main__.Net object at 0x10bd2f518>. Swap cost: -0.045621774431190365 round 8829: Swaping <__main__.Net object at 0x10bd2f518> and <__main__.Net obje

round 8885: Swaping <__main__.Net object at 0x10bd2f518> and <__main__.Net object at 0x10c776400>. Swap cost: -0.0038451724553718036 round 8886: Swaping <__main__.Net object at 0x10c776400> and <__main__.Net object at 0x10d7fdda0>. Swap cost: -0.025342066300277133 round 8887: Swaping <__main__.Net object at 0x10d7fdda0> and <__main__.Net object at 0x10bbd2630>. Swap cost: -0.0436880834128488 round 8888: Swaping <__main__.Net object at 0x10bbd2630> and <__main__.Net object at 0x10bd2f518>. Swap cost: -0.045621774431190365 round 8889: Swaping <__main__.Net object at 0x10bd2f518> and <__main__.Net object at 0x10c776400>. Swap cost: -0.0038451724553718036 round 8890: Swaping <__main__.Net object at 0x10c776400> and <__main__.Net object at 0x10d7fdda0>. Swap cost: -0.025342066300277133 round 8891: Swaping <__main__.Net object at 0x10d7fdda0> and <__main__.Net object at 0x10bbd2630>. Swap cost: -0.0436880834128488 round 8892: Swaping <__main__.Net object at 0x10bbd2630> and <__main__.Net obj

Swaping <__main__.Net object at 0x10bbd2630> and <__main__.Net object at 0x10bd2f518>. Swap cost: -0.045621774431190365 round 8949: Swaping <__main__.Net object at 0x10bd2f518> and <__main__.Net object at 0x10c776400>. Swap cost: -0.0038451724553718036 round 8950: Swaping <__main__.Net object at 0x10c776400> and <__main__.Net object at 0x10d7fdda0>. Swap cost: -0.025342066300277133 round 8951: Swaping <__main__.Net object at 0x10d7fdda0> and <__main__.Net object at 0x10bbd2630>. Swap cost: -0.0436880834128488 round 8952: Swaping <__main__.Net object at 0x10bbd2630> and <__main__.Net object at 0x10bd2f518>. Swap cost: -0.045621774431190365 round 8953: Swaping <__main__.Net object at 0x10bd2f518> and <__main__.Net object at 0x10c776400>. Swap cost: -0.0038451724553718036 round 8954: Swaping <__main__.Net object at 0x10c776400> and <__main__.Net object at 0x10d7fdda0>. Swap cost: -0.025342066300277133 round 8955: Swaping <__main__.Net object at 0x10d7fdda0> and <__main__.Net object at 0x1

round 9011: Swaping <__main__.Net object at 0x10d7fdda0> and <__main__.Net object at 0x10bbd2630>. Swap cost: -0.0436880834128488 round 9012: Swaping <__main__.Net object at 0x10bbd2630> and <__main__.Net object at 0x10bd2f518>. Swap cost: -0.045621774431190365 round 9013: Swaping <__main__.Net object at 0x10bd2f518> and <__main__.Net object at 0x10c776400>. Swap cost: -0.0038451724553718036 round 9014: Swaping <__main__.Net object at 0x10c776400> and <__main__.Net object at 0x10d7fdda0>. Swap cost: -0.025342066300277133 round 9015: Swaping <__main__.Net object at 0x10d7fdda0> and <__main__.Net object at 0x10bbd2630>. Swap cost: -0.0436880834128488 round 9016: Swaping <__main__.Net object at 0x10bbd2630> and <__main__.Net object at 0x10bd2f518>. Swap cost: -0.045621774431190365 round 9017: Swaping <__main__.Net object at 0x10bd2f518> and <__main__.Net object at 0x10c776400>. Swap cost: -0.0038451724553718036 round 9018: Swaping <__main__.Net object at 0x10c776400> and <__main__.Net obj

KeyboardInterrupt: 

In [27]:
a = [1, 2, 3, 4]
a[:-1]

[1, 2, 3]

In [131]:
a = 'e'
a += 'e'
print(a)

ee
